Load client_id and client_secret from the environment variables

In [1]:
from dotenv import load_dotenv
import os

load_dotenv()

client_id = os.getenv("CLIENT_ID")
client_secret = os.getenv("CLIENT_SECRET")

Authentication routine

In [2]:
import requests

url = "https://auth.smart.iec.ch/realms/iec/protocol/openid-connect/token"
data = {
    "client_id": client_id,
    "client_secret": client_secret,
    "grant_type": "client_credentials",
    "scope": "openid"
}

response = requests.post(url, data=data)
response.raise_for_status()
access_token = response.json().get("access_token")

print("Access Token:", access_token)

Access Token: eyJhbGciOiJSUzI1NiIsInR5cCIgOiAiSldUIiwia2lkIiA6ICI4aDNjSGQwZG8wYkdnSDE2MWhLVk1rcUhvTzlJWExoQktKOFRNUVBpcDJNIn0.eyJleHAiOjE3NTA0MDUzMTAsImlhdCI6MTc1MDQwMTcxMCwianRpIjoiMTI1MjE3MmQtNzk1Yi00NTZjLTk0NzgtNWQ4NTA1ZTA4MzIyIiwiaXNzIjoiaHR0cHM6Ly9hdXRoLnNtYXJ0LmllYy5jaC9yZWFsbXMvaWVjIiwiYXVkIjoiYWNjb3VudCIsInN1YiI6ImMxODA2N2EyLTU5NTUtNDVjMC04YzVhLWVjMjk1NDdhNzY1YyIsInR5cCI6IkJlYXJlciIsImF6cCI6InNtYXJ0LWVuYWJsZWQtYXBpIiwiYWNyIjoiMSIsImFsbG93ZWQtb3JpZ2lucyI6WyIvKiJdLCJyZWFsbV9hY2Nlc3MiOnsicm9sZXMiOlsiZGVmYXVsdC1yb2xlcy1pZWMiLCJvZmZsaW5lX2FjY2VzcyIsImFsbG93X2FsbF9zdGFuZGFyZHMiLCJ1bWFfYXV0aG9yaXphdGlvbiIsImFsbG93X2xvZ2luIl19LCJyZXNvdXJjZV9hY2Nlc3MiOnsiYWNjb3VudCI6eyJyb2xlcyI6WyJtYW5hZ2UtYWNjb3VudCIsIm1hbmFnZS1hY2NvdW50LWxpbmtzIiwidmlldy1wcm9maWxlIl19fSwic2NvcGUiOiJvcGVuaWQgZW1haWwgcHJvZmlsZSIsInNhbGVzX29yZ19pZCI6Ijk3Y2UxN2E2LWZkYmEtNGYwYi1iOTA4LTMwNTQ5NTIwNTUxZiIsImVtYWlsX3ZlcmlmaWVkIjpmYWxzZSwiY2xpZW50SG9zdCI6IjUxLjE1NC40Mi4yMzAiLCJyb2xlcyI6WyJkZWZhdWx0LXJvbGVzLWllYyIsIm9mZmxpbmVfYW

Get the list of clauses for the standard

In [11]:
standard_urn = "urn:iec:std:iec:60601-1:2005-12"

api_url = f"https://sim-apim.azure-api.net/preprod/v1/standards/{standard_urn}/clauses"
headers = {
    "Authorization": f"Bearer {access_token}"
}

api_response = requests.get(api_url, headers=headers)
api_response.raise_for_status()
print(api_response.json())

{'@context': {'comprisesClause': {'@type': '@id', '@id': 'corext:comprisesClause'}, 'dcterms': 'http://purl.org/dc/terms/', 'withinClause': {'@type': '@id', '@id': 'core:withinClause'}, 'hasTest': {'@type': '@id', '@id': 'ca:hasTest'}, 'ca': 'http://purl.org/smart-standards/ca#', 'core': 'http://purl.org/smart-standards/core#', 'rdfs': 'http://www.w3.org/2000/01/rdf-schema#', 'trans': 'http://iec.ch/smart/transformation#', 'hydra': 'http://www.w3.org/ns/hydra/core#', 'corext': 'http://purl.org/smart-standards/core/extension#', 'belongsToStandard': {'@type': '@id', '@id': 'core:belongsToStandard'}, 'hasMeasurement': {'@type': '@id', '@id': 'ca:hasMeasurement'}}, 'hydra:totalItems': 1002, '@graph': [{'@id': 'http://smart.iec.ch/clause/d2370186-f4b8-4bba-b308-b18975249f64', '@type': 'corext:Foreword', 'trans:sortKey': 'IEC60601120050000000003', 'rdfs:label': '', 'dcterms:title': 'FOREWORD', 'trans:checksum': 'ec80ecb8f195c272229ab4845518e601071b3cc22999fe396acd8dfb00664322', 'belongsToSta

Find the Foreword and extract the id

In [13]:
response = api_response.json()

# Extract the ID of the clause with type "corext:Foreword"
foreword_id = next(
    (item['@id'] for item in response.get('@graph', []) if item.get('@type') == 'corext:Foreword'),
    None
)

foreword_urn = foreword_id.rsplit('/', 1)[-1]

print("Foreword URN:", foreword_urn)

Foreword URN: d2370186-f4b8-4bba-b308-b18975249f64


Get the Foreword content

In [14]:
api_url = f"https://sim-apim.azure-api.net/preprod/v1/standards/{standard_urn}/clauses/{foreword_urn}"

api_response = requests.get(api_url, headers=headers)
api_response.raise_for_status()
print(api_response.json())

{'@id': 'http://smart.iec.ch/clause/d2370186-f4b8-4bba-b308-b18975249f64', '@type': 'corext:Foreword', 'trans:sortKey': 'IEC60601120050000000003', 'rdfs:label': '', 'dcterms:title': 'FOREWORD', 'trans:checksum': 'ec80ecb8f195c272229ab4845518e601071b3cc22999fe396acd8dfb00664322', 'belongsToStandard': 'http://smart.iec.ch/publication/urn:iec:std:iec:60601-1:2005-12', 'core:comprises': [{'@id': 'http://smart.iec.ch/provisionset/5159e1d7-6a0e-4642-8b86-b445f0668a24', '@type': 'corext:List', 'trans:sortKey': 'IEC60601120050000000004', 'core:comprisesProvisionSet': [{'@id': 'http://smart.iec.ch/provisionset/70c4a0fd-eb65-4f11-90ac-dc3d6a7409ed', '@type': 'corext:ListItem', 'trans:sortKey': 'IEC60601120050000000005', 'core:comprisesProvisionSet': [{'@id': 'http://smart.iec.ch/provisionset/b7786d7f-fcf8-4116-9111-198f41c8bb33', '@type': 'corext:Paragraph', 'trans:sortKey': 'IEC60601120050000000006', 'core:comprisesProvision': [{'@id': 'http://smart.iec.ch/provision/c539c84d-4b86-4333-8505-5ab6